
# Catch a Volatility Contraction Pattern (VCP) in Taiwan Market

## Selection Criteria:
1. **2nd Stage**: Stock should be in the second stage of an uptrend.
2. **VCP (Volatility Contraction Pattern)**:
   - Decreased trading volume 
   - Price range contraction  
     
3. **Strong Fundamental Support**: Solid financials, positive industry trends

In [100]:
import numpy as np
from finlab import data, backtest

close =  data.get('price:收盤價')
volume = data.get('price:成交股數')
revenue = data.get('monthly_revenue:當月營收')

Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.


## exmaple for rescaling

In [ ]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from datetime import timedelta

# Assuming normalize_window is a predefined function for normalizing the price window
def normalize_window(window):
    return (window - window.min()) / (window.max() - window.min())

# Assuming adj_close is your DataFrame containing the stock data
stock_data = adj_close[adj_close.code=='2330'].reset_index(drop=True)

# Ensure that stock_data has a DatetimeIndex
stock_data['date'] = pd.to_datetime(stock_data['date'])  # Convert to datetime if necessary
stock_data.set_index('date', inplace=True)  # Set the Date column as the index

# Ensure start_date and end_date are Timestamps
end_date = stock_data.index[-1]  # The last date in the stock data
start_date = end_date - timedelta(days=251)  # Define the window start

# Use .loc for slicing, and make sure the start and end dates are within the range of stock_data's index
window = stock_data.loc[start_date:end_date, 'adj_close']  # Extract 'adj_close' column over the time window

# Normalize the price window
normalized_prices = normalize_window(window)
normalized_time = np.linspace(0, 1, len(normalized_prices))  # Normalize time to the range [0, 1]

# Plot for Original Prices (P_T)
fig1 = go.Figure()

# Add original prices trace
fig1.add_trace(go.Scatter(
    x=window.index, y=window,
    mode='lines',
    name='Original Prices (P_T)',  # Label for original prices
    line=dict(color='gray')
))

fig1.update_layout(
    title=f'2330.TW Original Adjusted Stock Prices for {end_date.strftime("%Y-%m-%d")}',
    xaxis_title='Date',
    yaxis_title='Price',
    # template='plotly_white',
    hovermode='x unified'  # Show hover information for all traces at the same x-axis point
)

# Show the first figure (Original Prices)
fig1.show()

# Plot for Normalized Prices (\widetilde{P_T}) (Square plot)
fig2 = go.Figure()

# Add normalized prices trace
fig2.add_trace(go.Scatter(
    x=normalized_time, y=normalized_prices,
    mode='lines',
    name='Normalized Prices (\\widetilde{P_T})',  # Label for normalized prices
    line=dict(color='red', dash='dash')
))

fig2.update_layout(
    title=f'2330.TW Normalized Adjusted Stock Prices for {end_date.strftime("%Y-%m-%d")}',
    xaxis_title='Normalized Time (0-1)',
    yaxis_title='Normalized Price',
    # template='plotly_white', 
    hovermode='x unified',  # Show hover information for all traces at the same x-axis point
    xaxis=dict(range=[0, 1]),  # Ensure x-axis is between 0 and 1
    yaxis=dict(range=[0, 1]),  # Ensure y-axis is between 0 and 1
    width=600,  # Set the width to make the plot square
    height=600  # Set the height to make the plot square
)


# Show the second figure (Normalized Prices)
fig2.show()


In [1]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from datetime import datetime, timedelta
import matplotlib.pyplot as plt
import finlab
from finlab import data, backtest
import requests
import datetime as dt
from functools import reduce

def data_transform(df,col_name):
    
    filtered_col = [col for col in df.loc[:,'1101':].columns if col.isdigit() and 1000 <= int(col) <= 9999]
    df = df[filtered_col]
    df = df.reset_index().melt(id_vars=['date'], var_name='symbol', value_name=col_name)
    df = df.rename(columns={'symbol':'code'})
    return df

token = '5fN8Mb9iYba4vJdm6Q/Q1JNS0rCywzDmlJk7DCw9xNjay7xXeXzjPWmyWxMDv2+s#vip_m'
finlab.login(token)

close =  data.get('price:收盤價')
volume = data.get('price:成交股數')
revenue = data.get('monthly_revenue:當月營收')

輸入成功!


Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.


## Filter 01: 2nd Stage

In [2]:
stage_2 = (volume*close > 2000000) & (close > close.average(250))


## Filter 02: VCP

### 1. Decreasing trading volume

In [3]:
volumereduce = volume.average(10) < (volume.average(60)*0.5)

### 2. Price range contracton

#### Stamps

In [4]:
import plotly.graph_objs as go

# Define the function for plotting with shrinking wavelength
def custom_function_shrinking_wavelength(x, k, max_amplitude=1, contraction_rate=0.9):
    """
    Generate a function with shrinking wavelength (distance between peaks and valleys) from left to right.
    
    Arguments:
    x : ndarray
        Independent variable.
    k : float
        Controls the range of the function.
    max_amplitude : float
        Maximum initial amplitude (default is 1).
    contraction_rate : float
        Rate of amplitude contraction, controlling how the amplitude shrinks over time.
        
    Returns:
    f_x : ndarray
        The computed function values with shrinking wavelength.
    """
    # Increase frequency as x increases to shrink the wavelength
    frequency = 3 * np.pi * (1 + x)  # Frequency increases with x, shrinking the wavelength
    amplitude = max_amplitude * (contraction_rate ** x)  # Optional: Decrease amplitude over time
    return - (np.cos(frequency) ** 2) ** x / x * amplitude

# Normalize the function values between 0 and 1 using min-max normalization
def normalize_min_max(x, y):
    x_normalized = (x - np.min(x)) / (np.max(x) - np.min(x))
    y_normalized = (y - np.min(y)) / (np.max(y) - np.min(y))
    return x_normalized, y_normalized

# Set up the x values for the plot
k_values = [2, 3, 4, 5]  # Define k values
x_start, x_end = 0.5, 0.5 + 1/3  # x range

# Plot each value of k separately
for k in k_values:
    x = np.linspace(x_start, x_end + (k - 1) * 1/3, 125)  # Define x range for the specific k
    y = custom_function_shrinking_wavelength(x, k)
    
    # Normalize y values using min-max normalization
    x_normalized, y_normalized = normalize_min_max(x, y)
    
    # Create trace for the plot
    trace = go.Scatter(
        x=x_normalized,
        y=y_normalized,
        mode='lines',
        name=f'k = {k}',
        line=dict(color='black')
    )

    # Create layout for the plot
    layout = go.Layout(
        title=f"Custom Function Plot (Shrinking Wavelength) for k = {k}",
        showlegend=True,
        xaxis=dict(range=[0, 1], title="Normalized x"),  # Ensure x-axis is between 0 and 1
        yaxis=dict(range=[0, 1], title="Normalized f(x)"),  # Ensure y-axis is between 0 and 1
        width=600,  # Set the width to make the plot square
        height=600  # Set the height to make the plot square
    )

    # Create the figure and display it
    fig = go.Figure(data=[trace], layout=layout)
    fig.show()


#### Algo

In [5]:
close = close[close.index > '2014-01-01']

## calculate cosine similarity

In [6]:
def custom_function_shrinking_wavelength(x, k):
    # Increase frequency as x increases to shrink the wavelength
    frequency = 3 * np.pi * (1 + x)  # Frequency increases with x, shrinking the wavelength
    return - (np.cos(frequency) ** 2) ** x / x

# Normalize the function values between 0 and 1 using min-max normalization
def normalize_min_max(x, y):
    x_normalized = (x - np.min(x)) / (np.max(x) - np.min(x))
    y_normalized = (y - np.min(y)) / (np.max(y) - np.min(y))
    return x_normalized, y_normalized

# Set up the x values for the plot
k_values = [2, 3, 4, 5, 6, 7, 8, 9, 10]  # Define k values
x_start, x_end = 0.5, 0.5 + 1/3  # x range
vcp_template = pd.DataFrame()

for k in k_values:
    x = np.linspace(x_start, x_end + (k - 1) * 1/3, 125)  # Define x range for the specific k
    y = custom_function_shrinking_wavelength(x, k)
    
    # Normalize y values using min-max normalization
    x_normalized, y_normalized = normalize_min_max(x, y)
    vcp_template[f'{k}'] = y_normalized
    vcp_template.columns.name='k'

In [7]:
vcp_template.head()

k         2         3         4         5         6         7         8  \
0  1.000000  1.000000  1.000000  1.000000  1.000000  1.000000  1.000000   
1  0.935908  0.905358  0.875473  0.846091  0.817134  0.789621  0.762061   
2  0.875487  0.817766  0.762061  0.707974  0.655323  0.606014  0.557265   
3  0.817703  0.735096  0.656356  0.580918  0.508620  0.442322  0.378252   
4  0.762088  0.656513  0.557265  0.463838  0.376383  0.298934  0.227182   

k         9        10  
0  1.000000  1.000000  
1  0.734100  0.707463  
2  0.508475  0.462900  
3  0.315828  0.259849  
4  0.160984  0.106772

In [42]:
from sklearn.metrics.pairwise import cosine_similarity

# 假設模板數據 vcp_template 已經是 DataFrame
template_data = {str(k): vcp_template[k].values for k in vcp_template.columns}

# 定義餘弦相似度計算函數
def calculate_similarity(stock_vector, templates):
    # 處理 NaN 值，將其替換為列的平均值或 0
    stock_vector = np.nan_to_num(stock_vector, nan=np.nanmean(stock_vector))
    
    scores = []
    for k, template in templates.items():
        
        min_len = min(len(stock_vector), len(template))
        similarity = cosine_similarity(
            stock_vector[-min_len:].reshape(1, -1), 
            template[:min_len].reshape(1, -1)
        )[0][0]
        scores.append(similarity)
    return max(scores)

def normalize_window(window):
    if window.max() > window.min():
        return (window[-1] - window.min()) / (window.max() - window.min())
    else:
        return 0  # 避免所有值相同時的除以零錯誤

rolling_normalized_data = close.tail(125).rolling(window=125, min_periods=1).apply(normalize_window, raw=False)
# 過濾掉含有 NaN 的列
rolling_normalized_data = rolling_normalized_data.dropna(axis=1, how="any")
display(rolling_normalized_data)
# 計算相似度
similarity_scores = rolling_normalized_data.apply(
    lambda col: calculate_similarity(col.values, template_data),
    axis=0  # Apply along columns
)

symbol          0050      0051      0052      0053      0055      0056  \
date                                                                     
2024-06-05  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2024-06-06  1.000000  1.000000  1.000000  1.000000  1.000000  1.000000   
2024-06-07  0.765217  1.000000  0.692982  0.653846  1.000000  0.789474   
2024-06-11  0.843478  0.562500  0.807018  0.846154  1.000000  0.473684   
2024-06-12  1.000000  0.437500  1.000000  1.000000  0.781818  0.578947   
...              ...       ...       ...       ...       ...       ...   
2024-12-02  0.748864  0.294574  0.722164  0.628631  0.501433  0.253316   
2024-12-03  0.807955  0.341085  0.779396  0.682573  0.581662  0.257294   
2024-12-04  0.834091  0.375969  0.821020  0.707469  0.578797  0.262599   
2024-12-05  0.857955  0.387597  0.839750  0.732365  0.613181  0.278515   
2024-12-06  0.840909  0.383721  0.812695  0.701245  0.618911  0.290451   

symbol          0057      0061    006201    006203  ...   9942      9943  \
date                                                ...                    
2024-06-05  0.000000  0.000000  0.000000  0.000000  ...  0.000  0.000000   
2024-06-06  1.000000  1.000000  0.000000  1.000000  ...  0.000  1.000000   
2024-06-07  0.766234  0.000000  1.000000  0.760000  ...  1.000  1.000000   
2024-06-11  0.909091  0.000000  1.000000  0.940000  ...  1.000  0.000000   
2024-06-12  1.000000  0.000000  1.000000  1.000000  ...  0.000  0.000000   
...              ...       ...       ...       ...  ...    ...       ...   
2024-12-02  0.753769  0.327962  0.413136  0.730964  ...  0.175  0.073770   
2024-12-03  0.815745  0.331754  0.413136  0.804569  ...  0.200  0.081967   
2024-12-04  0.839196  0.326066  0.504237  0.804569  ...  0.200  0.049180   
2024-12-05  0.879397  0.311848  0.533898  0.855330  ...  0.225  0.049180   
2024-12-06  0.849246  0.341232  0.497881  0.819797  ...  0.250  0.073770   

symbol          9944      9945      9946      9950  9951      9955      9958  \
date                                                                           
2024-06-05  0.000000  0.000000  0.000000  0.000000   0.0  0.000000  0.000000   
2024-06-06  0.000000  0.000000  0.000000  0.000000   0.0  1.000000  1.000000   
2024-06-07  1.000000  1.000000  1.000000  0.111111   1.0  1.000000  1.000000   
2024-06-11  0.000000  0.320000  0.000000  0.000000   0.0  0.000000  1.000000   
2024-06-12  0.583333  0.000000  0.000000  0.000000   1.0  0.000000  1.000000   
...              ...       ...       ...       ...   ...       ...       ...   
2024-12-02  0.179487  0.221053  0.097786  0.000000   0.0  0.000000  0.026316   
2024-12-03  0.166667  0.257895  0.103321  0.000000   0.0  0.021277  0.031579   
2024-12-04  0.153846  0.263158  0.070111  0.000000   0.0  0.042553  0.047368   
2024-12-05  0.153846  0.236842  0.055351  0.000000   0.0  0.058511  0.031579   
2024-12-06  0.179487  0.305263  0.099631  0.019417   0.0  0.015957  0.021053   

symbol          9962  
date                  
2024-06-05  0.000000  
2024-06-06  0.000000  
2024-06-07  1.000000  
2024-06-11  0.000000  
2024-06-12  0.500000  
...              ...  
2024-12-02  0.304348  
2024-12-03  0.369565  
2024-12-04  0.413043  
2024-12-05  0.434783  
2024-12-06  0.413043  

[125 rows x 1862 columns]

In [73]:
# 定义归一化函数
def normalize_window(window):
    if window.max() > window.min():
        return (window[-1] - window.min()) / (window.max() - window.min())
    else:
        return 0  # 避免所有值相同时的除以零错误

# 计算滚动归一化值
rolling_normalized_data = close.rolling(window=125, min_periods=1).apply(normalize_window, raw=False)
# 过滤掉含有 NaN 的列
rolling_normalized_data = rolling_normalized_data.dropna(axis=1, how="any")

In [74]:
rolling_normalized_data

symbol          0050      0055      0056      0061    006205    006206  \
date                                                                     
2014-01-02  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2014-01-03  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2014-01-06  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2014-01-07  0.000000  0.333333  0.366667  0.100000  0.481481  0.000000   
2014-01-08  0.117647  0.259259  0.833333  0.150000  0.740741  0.207547   
...              ...       ...       ...       ...       ...       ...   
2024-12-02  0.748864  0.561713  0.253316  0.327962  0.479828  0.402742   
2024-12-03  0.807955  0.596685  0.257294  0.331754  0.489270  0.404456   
2024-12-04  0.834091  0.593923  0.262599  0.326066  0.481545  0.409597   
2024-12-05  0.857955  0.627072  0.278515  0.311848  0.466094  0.390746   
2024-12-06  0.840909  0.618911  0.290451  0.341232  0.500429  0.420737   

symbol        006207      1104      1108      1201  ...      9938      9939  \
date                                                ...                       
2014-01-02  0.000000  0.000000  0.000000  0.000000  ...  0.000000  0.000000   
2014-01-03  0.000000  0.000000  0.000000  0.000000  ...  0.000000  1.000000   
2014-01-06  0.000000  0.000000  0.000000  0.000000  ...  0.222222  0.000000   
2014-01-07  0.000000  1.000000  0.600000  0.285714  ...  1.000000  0.571429   
2014-01-08  0.281250  0.692308  0.000000  0.000000  ...  0.000000  1.000000   
...              ...       ...       ...       ...  ...       ...       ...   
2024-12-02  0.484064  0.025316  0.038462  0.393939  ...  0.904167  0.056604   
2024-12-03  0.488048  0.050633  0.038462  0.424242  ...  1.000000  0.056604   
2024-12-04  0.478088  0.075949  0.038462  0.424242  ...  1.000000  0.075472   
2024-12-05  0.460159  0.069620  0.038462  0.518519  ...  0.947761  0.056604   
2024-12-06  0.496016  0.044304  0.038462  0.538462  ...  0.914179  0.075472   

symbol          9940      9941      9942      9944      9946  9951      9955  \
date                                                                           
2014-01-02  0.000000  0.000000  0.000000  0.000000  0.000000   0.0  0.000000   
2014-01-03  0.000000  0.000000  1.000000  0.000000  0.000000   0.0  1.000000   
2014-01-06  0.000000  0.090909  0.000000  0.090909  0.000000   0.0  0.500000   
2014-01-07  0.277778  0.000000  0.238095  0.000000  0.000000   0.1  1.000000   
2014-01-08  0.166667  0.166667  0.095238  0.230769  0.222222   0.1  0.666667   
...              ...       ...       ...       ...       ...   ...       ...   
2024-12-02  0.064748  0.032258  0.175000  0.179487  0.097786   0.0  0.000000   
2024-12-03  0.093525  0.043011  0.200000  0.166667  0.103321   0.0  0.021277   
2024-12-04  0.100719  0.021505  0.200000  0.153846  0.070111   0.0  0.042553   
2024-12-05  0.107914  0.000000  0.225000  0.153846  0.055351   0.0  0.058511   
2024-12-06  0.093525  0.000000  0.250000  0.179487  0.099631   0.0  0.015957   

symbol          9958  
date                  
2014-01-02  0.000000  
2014-01-03  0.000000  
2014-01-06  0.000000  
2014-01-07  0.000000  
2014-01-08  0.000000  
...              ...  
2024-12-02  0.026316  
2024-12-03  0.031579  
2024-12-04  0.047368  
2024-12-05  0.031579  
2024-12-06  0.021053  

[2670 rows x 670 columns]

In [65]:
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import pandas as pd

# 假设模板数据 vcp_template 已经是 DataFrame
template_data = {str(k): vcp_template[k].values for k in vcp_template.columns}

# 定义余弦相似度计算函数
def calculate_similarity(stock_vector, templates):
    # 处理 NaN 值，替换为列的平均值或 0
    stock_vector = np.nan_to_num(stock_vector, nan=np.nanmean(stock_vector))
    
    scores = []
    for k, template in templates.items():
        min_len = min(len(stock_vector), len(template))
        similarity = cosine_similarity(
            stock_vector[-min_len:].reshape(1, -1),
            template[:min_len].reshape(1, -1)
        )[0][0]
        scores.append(similarity)
    return max(scores)


# 创建一个与 rolling_normalized_data 结构相同的 DataFrame，用于存储相似度结果
similarity_scores = pd.DataFrame(index=rolling_normalized_data.index, columns=rolling_normalized_data.columns)

# 每五天计算一次相似度
for i in range(0, (len(rolling_normalized_data)-125), 5):  # 每五天处理一次

    current_window = rolling_normalized_data.iloc[i:125+i,:]
    scores = current_window.apply(
    lambda col: calculate_similarity(col.values, template_data)
    )

    target_index = similarity_scores.index[125 + i]  # 取当前计算窗口的最后一天
    similarity_scores.loc[target_index] = scores
    print(scores)
    

0
symbol
0050    0.880856
0051    0.872922
0052    0.874266
0053    0.873387
0055    0.945047
          ...   
9950    0.673372
9951    0.641785
9955    0.941767
9958    0.698501
9962    0.744140
Length: 1844, dtype: float64
5
symbol
0050    0.895055
0051    0.871379
0052    0.889486
0053    0.889170
0055    0.944861
          ...   
9950    0.626444
9951    0.617506
9955    0.935326
9958    0.682341
9962    0.735654
Length: 1844, dtype: float64
10
symbol
0050    0.894303
0051    0.863314
0052    0.889038
0053    0.886475
0055    0.950356
          ...   
9950    0.650656
9951    0.611700
9955    0.910899
9958    0.647088
9962    0.789900
Length: 1844, dtype: float64
15
symbol
0050    0.904476
0051    0.860020
0052    0.898031
0053    0.891832
0055    0.954661
          ...   
9950    0.619112
9951    0.563451
9955    0.919646
9958    0.631012
9962    0.836084
Length: 1844, dtype: float64
20
symbol
0050    0.908331
0051    0.865135
0052    0.902382
0053    0.894491
0055    0.941552
   

In [80]:
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import pandas as pd

# 假设模板数据 vcp_template 已经是 DataFrame
template_data = {str(k): vcp_template[k].values for k in vcp_template.columns}

# 定义余弦相似度计算函数
def calculate_similarity(stock_vector, templates):
    # 处理 NaN 值，替换为列的平均值或 0
    stock_vector = np.nan_to_num(stock_vector, nan=np.nanmean(stock_vector))
    
    scores = []
    for k, template in templates.items():
        min_len = min(len(stock_vector), len(template))
        similarity = cosine_similarity(
            stock_vector[-min_len:].reshape(1, -1),
            template[:min_len].reshape(1, -1)
        )[0][0]
        scores.append(similarity)
    return max(scores)


# 创建一个与 rolling_normalized_data 结构相同的 DataFrame，用于存储相似度结果
similarity_scores = pd.DataFrame(index=rolling_normalized_data.index, columns=rolling_normalized_data.columns)

# 每五天计算一次相似度
for i in range(0, (len(rolling_normalized_data)-125), 5):  # 每五天处理一次

    current_window = rolling_normalized_data.iloc[i:125+i,:]
    scores = current_window.apply(
    lambda col: calculate_similarity(col.values, template_data)
    )

    target_index = similarity_scores.index[125 + i]  # 取当前计算窗口的最后一天
    similarity_scores.loc[target_index] = scores    

similarity_scores = similarity_scores.ffill()

## Filter 03: Strong Fundamental Support

In [85]:
strong_fund = (revenue.pct_change().average(6) > 0).index_str_to_date()

## backtest

In [94]:
close[close.index>='2015-01-01']

symbol      0015    0050   0051    0052    0053   0054   0055   0056    0057  \
date                                                                           
2015-01-05   NaN   66.55  29.80   42.00   28.85  22.16  14.50  24.15   40.89   
2015-01-06   NaN   64.90  29.20   40.83   28.29  21.90  14.21  23.89   39.78   
2015-01-07   NaN   65.00  29.29   41.07   28.49  21.85  14.22  23.91   39.92   
2015-01-08   NaN   66.50  29.80   42.20   28.97  22.20  14.38  24.12   40.84   
2015-01-09   NaN   66.15  29.85   41.67   28.83  22.48  14.41  24.16   40.74   
...          ...     ...    ...     ...     ...    ...    ...    ...     ...   
2024-12-02   NaN  191.70  77.45  188.15  101.15    NaN  28.17  37.02  140.80   
2024-12-03   NaN  194.30  78.05  190.90  102.45    NaN  28.45  37.05  142.65   
2024-12-04   NaN  195.45  78.50  192.90  103.05    NaN  28.44  37.09  143.35   
2024-12-05   NaN  196.50  78.65  193.80  103.65    NaN  28.56  37.21  144.55   
2024-12-06   NaN  195.75  78.60  192.50  102.90    NaN  28.58  37.30  143.65   

symbol       0058  ...   9944   9945   9946   9949   9950   9951   9955  \
date               ...                                                    
2015-01-05  37.46  ...  45.75  50.00  21.70  20.25  23.70  112.5  18.40   
2015-01-06  36.88  ...  45.90  48.95  21.10  19.75  23.65  110.5  18.55   
2015-01-07  36.81  ...  46.30  49.00  21.00  19.50  23.60  113.0  18.65   
2015-01-08  37.38  ...  45.85  49.40  20.60  19.80  23.60  113.5  18.60   
2015-01-09  37.54  ...  45.00  49.30  20.70  19.70  23.75  113.5  18.60   
...           ...  ...    ...    ...    ...    ...    ...    ...    ...   
2024-12-02    NaN  ...  20.60  45.40  25.10  25.90  13.00   59.2  29.35   
2024-12-03    NaN  ...  20.55  45.75  25.25  25.85  13.00   59.1  29.55   
2024-12-04    NaN  ...  20.50  45.80  24.35  25.80  13.00   59.1  29.75   
2024-12-05    NaN  ...  20.50  45.55  23.95  26.00  12.85   58.7  29.90   
2024-12-06    NaN  ...  20.60  46.20  25.15  25.35  12.95   58.7  29.50   

symbol        9958   9960   9962  
date                              
2015-01-05   10.75  22.20  11.60  
2015-01-06   10.60  22.40  11.55  
2015-01-07   10.50  22.00  11.55  
2015-01-08   10.45  22.50  11.65  
2015-01-09   10.50  22.50  11.60  
...            ...    ...    ...  
2024-12-02  180.00  26.05  15.35  
2024-12-03  181.00  26.30  15.50  
2024-12-04  184.00  26.20  15.60  
2024-12-05  181.00  26.25  15.65  
2024-12-06  179.00  26.35  15.60  

[2422 rows x 2554 columns]

In [107]:
(similarity_scores).replace([np.inf, -np.inf], np.nan)

symbol          0050     0055      0056     0061    006205    006206  \
date                                                                   
2014-01-02       NaN      NaN       NaN      NaN       NaN       NaN   
2014-01-03       NaN      NaN       NaN      NaN       NaN       NaN   
2014-01-06       NaN      NaN       NaN      NaN       NaN       NaN   
2014-01-07       NaN      NaN       NaN      NaN       NaN       NaN   
2014-01-08       NaN      NaN       NaN      NaN       NaN       NaN   
...              ...      ...       ...      ...       ...       ...   
2024-12-02  0.921852  0.94218  0.806559  0.79995  0.837606  0.825965   
2024-12-03  0.921852  0.94218  0.806559  0.79995  0.837606  0.825965   
2024-12-04  0.921852  0.94218  0.806559  0.79995  0.837606  0.825965   
2024-12-05  0.921852  0.94218  0.806559  0.79995  0.837606  0.825965   
2024-12-06  0.921852  0.94218  0.806559  0.79995  0.837606  0.825965   

symbol        006207      1104      1108      1201  ...     9938      9939  \
date                                                ...                      
2014-01-02       NaN       NaN       NaN       NaN  ...      NaN       NaN   
2014-01-03       NaN       NaN       NaN       NaN  ...      NaN       NaN   
2014-01-06       NaN       NaN       NaN       NaN  ...      NaN       NaN   
2014-01-07       NaN       NaN       NaN       NaN  ...      NaN       NaN   
2014-01-08       NaN       NaN       NaN       NaN  ...      NaN       NaN   
...              ...       ...       ...       ...  ...      ...       ...   
2024-12-02  0.818237  0.622232  0.604272  0.866789  ...  0.92012  0.773019   
2024-12-03  0.818237  0.622232  0.604272  0.866789  ...  0.92012  0.773019   
2024-12-04  0.818237  0.622232  0.604272  0.866789  ...  0.92012  0.773019   
2024-12-05  0.818237  0.622232  0.604272  0.866789  ...  0.92012  0.773019   
2024-12-06  0.818237  0.622232  0.604272  0.866789  ...  0.92012  0.773019   

symbol          9940      9941      9942      9944      9946      9951  \
date                                                                     
2014-01-02       NaN       NaN       NaN       NaN       NaN       NaN   
2014-01-03       NaN       NaN       NaN       NaN       NaN       NaN   
2014-01-06       NaN       NaN       NaN       NaN       NaN       NaN   
2014-01-07       NaN       NaN       NaN       NaN       NaN       NaN   
2014-01-08       NaN       NaN       NaN       NaN       NaN       NaN   
...              ...       ...       ...       ...       ...       ...   
2024-12-02  0.691158  0.826106  0.835003  0.653447  0.681847  0.623638   
2024-12-03  0.691158  0.826106  0.835003  0.653447  0.681847  0.623638   
2024-12-04  0.691158  0.826106  0.835003  0.653447  0.681847  0.623638   
2024-12-05  0.691158  0.826106  0.835003  0.653447  0.681847  0.623638   
2024-12-06  0.691158  0.826106  0.835003  0.653447  0.681847  0.623638   

symbol          9955      9958  
date                            
2014-01-02       NaN       NaN  
2014-01-03       NaN       NaN  
2014-01-06       NaN       NaN  
2014-01-07       NaN       NaN  
2014-01-08       NaN       NaN  
...              ...       ...  
2024-12-02  0.891988  0.620946  
2024-12-03  0.891988  0.620946  
2024-12-04  0.891988  0.620946  
2024-12-05  0.891988  0.620946  
2024-12-06  0.891988  0.620946  

[2670 rows x 670 columns]

In [109]:
rank=(revenue / revenue.average(3)).replace([np.inf, -np.inf], np.nan).index_str_to_date()

In [129]:
similarity_scores.dropna()

symbol          0050      0055      0056      0061    006205    006206  \
date                                                                     
2014-07-10  0.970672  0.810253  0.940797  0.679717  0.612919  0.847145   
2014-07-11  0.970672  0.810253  0.940797  0.679717  0.612919  0.847145   
2014-07-14  0.970672  0.810253  0.940797  0.679717  0.612919  0.847145   
2014-07-15  0.970672  0.810253  0.940797  0.679717  0.612919  0.847145   
2014-07-16  0.970672  0.810253  0.940797  0.679717  0.612919  0.847145   
...              ...       ...       ...       ...       ...       ...   
2024-12-02  0.921852  0.942180  0.806559  0.799950  0.837606  0.825965   
2024-12-03  0.921852  0.942180  0.806559  0.799950  0.837606  0.825965   
2024-12-04  0.921852  0.942180  0.806559  0.799950  0.837606  0.825965   
2024-12-05  0.921852  0.942180  0.806559  0.799950  0.837606  0.825965   
2024-12-06  0.921852  0.942180  0.806559  0.799950  0.837606  0.825965   

symbol        006207      1104      1108      1201  ...      9938      9939  \
date                                                ...                       
2014-07-10  0.711740  0.784859  0.910733  0.733381  ...  0.948398  0.733064   
2014-07-11  0.711740  0.784859  0.910733  0.733381  ...  0.948398  0.733064   
2014-07-14  0.711740  0.784859  0.910733  0.733381  ...  0.948398  0.733064   
2014-07-15  0.711740  0.784859  0.910733  0.733381  ...  0.948398  0.733064   
2014-07-16  0.711740  0.784859  0.910733  0.733381  ...  0.948398  0.733064   
...              ...       ...       ...       ...  ...       ...       ...   
2024-12-02  0.818237  0.622232  0.604272  0.866789  ...  0.920120  0.773019   
2024-12-03  0.818237  0.622232  0.604272  0.866789  ...  0.920120  0.773019   
2024-12-04  0.818237  0.622232  0.604272  0.866789  ...  0.920120  0.773019   
2024-12-05  0.818237  0.622232  0.604272  0.866789  ...  0.920120  0.773019   
2024-12-06  0.818237  0.622232  0.604272  0.866789  ...  0.920120  0.773019   

symbol          9940      9941      9942      9944      9946      9951  \
date                                                                     
2014-07-10  0.843923  0.896011  0.951894  0.946199  0.649463  0.937997   
2014-07-11  0.843923  0.896011  0.951894  0.946199  0.649463  0.937997   
2014-07-14  0.843923  0.896011  0.951894  0.946199  0.649463  0.937997   
2014-07-15  0.843923  0.896011  0.951894  0.946199  0.649463  0.937997   
2014-07-16  0.843923  0.896011  0.951894  0.946199  0.649463  0.937997   
...              ...       ...       ...       ...       ...       ...   
2024-12-02  0.691158  0.826106  0.835003  0.653447  0.681847  0.623638   
2024-12-03  0.691158  0.826106  0.835003  0.653447  0.681847  0.623638   
2024-12-04  0.691158  0.826106  0.835003  0.653447  0.681847  0.623638   
2024-12-05  0.691158  0.826106  0.835003  0.653447  0.681847  0.623638   
2024-12-06  0.691158  0.826106  0.835003  0.653447  0.681847  0.623638   

symbol          9955      9958  
date                            
2014-07-10  0.613962  0.773136  
2014-07-11  0.613962  0.773136  
2014-07-14  0.613962  0.773136  
2014-07-15  0.613962  0.773136  
2014-07-16  0.613962  0.773136  
...              ...       ...  
2024-12-02  0.891988  0.620946  
2024-12-03  0.891988  0.620946  
2024-12-04  0.891988  0.620946  
2024-12-05  0.891988  0.620946  
2024-12-06  0.891988  0.620946  

[2545 rows x 670 columns]

In [148]:
check = pd.DataFrame(similarity_scores.tail(5).transpose())
check.sort_values(['2024-12-06']).tail(5)

date    2024-12-02  2024-12-03  2024-12-04  2024-12-05  2024-12-06
symbol                                                            
3167      0.961370    0.961370    0.961370    0.961370    0.961370
2357      0.962040    0.962040    0.962040    0.962040    0.962040
1708      0.963778    0.963778    0.963778    0.963778    0.963778
8069      0.965496    0.965496    0.965496    0.965496    0.965496
3450      0.966754    0.966754    0.966754    0.966754    0.966754

In [182]:
test_report

stock_id entry_date  exit_date entry_sig_date exit_sig_date  position  \
0     3303 岱稜 2015-09-21 2015-09-30     2015-09-18    2015-09-25       0.1   
1     3303 岱稜 2015-09-30 2015-10-05     2015-09-25    2015-10-02       0.1   
2     3303 岱稜 2015-10-05 2015-10-12     2015-10-02    2015-10-08       0.1   
3     3303 岱稜 2015-10-12 2015-10-19     2015-10-08    2015-10-16       0.1   
4     3303 岱稜 2015-10-19 2015-10-26     2015-10-16    2015-10-23       0.1   
...       ...        ...        ...            ...           ...       ...   
3016  1569 濱川 2024-12-02        NaT     2024-11-29           NaT       0.1   
3017  3450 聯鈞 2024-12-02        NaT     2024-11-29           NaT       0.1   
3018  4956 光鋐 2024-12-02        NaT     2024-11-29           NaT       0.1   
3019  6214 精誠        NaT        NaT     2024-12-08           NaT       NaN   
3020  9938 百和        NaT        NaT     2024-12-08           NaT       NaN   

      period  entry_index  exit_index    return  ... turnover@entry_date  \
0        5.0       2091.0      2096.0  0.010631  ...        1.341450e+07   
1        3.0       2096.0      2099.0 -0.030220  ...        1.062880e+07   
2        4.0       2099.0      2103.0  0.050992  ...        2.753418e+06   
3        5.0       2103.0      2108.0 -0.018868  ...        2.052094e+07   
4        5.0       2108.0      2113.0  0.016484  ...        2.530018e+06   
...      ...          ...         ...       ...  ...                 ...   
3016     5.0       4335.0        -1.0 -0.020062  ...        2.037534e+08   
3017     5.0       4335.0        -1.0  0.034560  ...        6.935998e+09   
3018     5.0       4335.0        -1.0  0.047753  ...        1.189600e+08   
3019     NaN          NaN         NaN       NaN  ...        2.164063e+09   
3020     NaN          NaN         NaN       NaN  ...        3.006653e+08   

      turnover@exit_date  volume@entry_date  volume@exit_date  警示股@entry_date  \
0           1.062880e+07           745250.0          584000.0           False   
1           2.753418e+06           584000.0          156001.0           False   
2           2.052094e+07           156001.0         1106250.0           False   
3           2.530018e+06          1106250.0          139012.0           False   
4           3.109776e+06           139012.0          168096.0           False   
...                  ...                ...               ...             ...   
3016        9.271438e+07          3144343.0         1460069.0           False   
3017        5.365832e+09         28602055.0        21377818.0           False   
3018        4.622545e+08          3341573.0        12392882.0           False   
3019        2.164063e+09         13783839.0        13783839.0           False   
3020        3.006653e+08          3666650.0         3666650.0           False   

      處置股@entry_date  全額交割股@entry_date  警示股@exit_date  處置股@exit_date  \
0              False             False          False          False   
1              False             False          False          False   
2              False             False          False          False   
3              False             False          False          False   
4              False             False          False          False   
...              ...               ...            ...            ...   
3016            True             False          False           True   
3017           False             False          False          False   
3018           False             False          False          False   
3019           False             False          False          False   
3020           False             False          False          False   

      全額交割股@exit_date  
0               False  
1               False  
2               False  
3               False  
4               False  
...               ...  
3016            False  
3017            False  
3018            False  
3019            False  
3020            False  

[3021 rows x 25 columns]

In [198]:
df/100

Jan    Feb    Mar    Apr    May    Jun    Jul    Aug    Sep    Oct  \
Year                                                                         
2015  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.001  0.000   
2016  0.011  0.040  0.082 -0.001  0.004 -0.017 -0.009 -0.005  0.001  0.043   
2017  0.078  0.100  0.003 -0.030  0.034  0.011  0.115  0.105  0.014  0.100   
2018  0.059 -0.095 -0.010 -0.014  0.038  0.050 -0.028 -0.030 -0.033 -0.039   
2019 -0.000  0.031 -0.003 -0.014 -0.014  0.007  0.098  0.000  0.021  0.068   
2020  0.014  0.017 -0.058  0.000  0.006 -0.008 -0.048  0.022 -0.067  0.003   
2021 -0.060  0.103  0.093  0.087 -0.136  0.050  0.040 -0.007  0.007 -0.019   
2022 -0.065  0.049  0.076 -0.033 -0.017 -0.042 -0.016  0.003 -0.076 -0.006   
2023  0.014  0.063  0.009  0.031  0.051  0.022  0.076 -0.001  0.004 -0.016   
2024  0.081  0.047 -0.038  0.018  0.000  0.099  0.026 -0.054 -0.068 -0.024   

        Nov    Dec  
Year                
2015 -0.020  0.009  
2016  0.024  0.040  
2017  0.009  0.033  
2018  0.000 -0.000  
2019  0.033  0.048  
2020  0.055  0.009  
2021  0.040  0.039  
2022  0.032 -0.049  
2023  0.019 -0.031  
2024  0.043  0.002

In [195]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt


# Create the data
data = {
    '2015': [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.1, 0.0, -2.0, 0.9],
    '2016': [1.1, 4.0, 8.2, -0.1, 0.4, -1.7, -0.9, -0.5, 0.1, 4.3, 2.4, 4.0],
    '2017': [7.8, 10.0, 0.3, -3.0, 3.4, 1.1, 11.5, 10.5, 1.4, 10.0, 0.9, 3.3],
    '2018': [5.9, -9.5, -1.0, -1.4, 3.8, 5.0, -2.8, -3.0, -3.3, -3.9, 0.0, -0.0],
    '2019': [-0.0, 3.1, -0.3, -1.4, -1.4, 0.7, 9.8, 0.0, 2.1, 6.8, 3.3, 4.8],
    '2020': [1.4, 1.7, -5.8, 0.0, 0.6, -0.8, -4.8, 2.2, -6.7, 0.3, 5.5, 0.9],
    '2021': [-6.0, 10.3, 9.3, 8.7, -13.6, 5.0, 4.0, -0.7, 0.7, -1.9, 4.0, 3.9],
    '2022': [-6.5, 4.9, 7.6, -3.3, -1.7, -4.2, -1.6, 0.3, -7.6, -0.6, 3.2, -4.9],
    '2023': [1.4, 6.3, 0.9, 3.1, 5.1, 2.2, 7.6, -0.1, 0.4, -1.6, 1.9, -3.1],
    '2024': [8.1, 4.7, -3.8, 1.8, 0.0, 9.9, 2.6, -5.4, -6.8, -2.4, 4.3, 0.2]
}

df = pd.DataFrame(data.items(), columns=['Year', 'Returns'])
df = pd.DataFrame(df['Returns'].tolist(), 
                 index=df['Year'],
                 columns=['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec'])

# Format the numbers to include % sign and show positive/negative
df_styled = df.style.format("{:+.1f}%".format)

# # Create a figure with larger size
# plt.figure(figsize=(15, 8))

# # Create a table plot
# table = plt.table(cellText=df_styled.data,
#                  rowLabels=df.index,
#                  colLabels=df.columns,
#                  cellLoc='center',
#                  loc='center',
#                  bbox=[0, 0, 1, 1])

# # Adjust table properties
# table.auto_set_font_size(False)
# table.set_fontsize(9)
# table.scale(1.2, 1.5)

# # Remove axes
# plt.axis('off')

# # Add title
# plt.title('Monthly Returns (%)', pad=20, fontsize=14)

# plt.show()

In [200]:
# 營收成長
c1 = (revenue.pct_change().average(6) > 0).index_str_to_date()
# c2 = close.rolling(20).min() > close.rolling(20).max() * 0.7
# 成交量與價格收縮
volumereduce = volume.average(10) < (volume.average(60)*0.5)
pricecontract = similarity_scores>0.9

# VCP = 價量收縮、創新高、有足夠成交量
vcp = (volumereduce & pricecontract).sustain(5, 1) & (close == close.rolling(100).max()) & (volume >= volume.rolling(20).mean()*0.8)

# 總體部位
# 進場：(c1, c2, vcp, 流動性足夠, 長期均向上)
# 出場：股價 < 季線
buy = (vcp & c1 & c2 & (volume*close > 2000000) & (close > close.average(250)))
sell = close < close.average(60)

p = buy.hold_until(sell, nstocks_limit=10, rank=(revenue / revenue.average(3)).replace([np.inf, -np.inf], np.nan).index_str_to_date())

# 回測
test_report, r = backtest.sim(p, fee_ratio=1.425/1000/3,position_limit=0.1, resample='W', stop_loss=0.1)

Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip

In [210]:
test_report.exit_date = pd.to_datetime(test_report.exit_date)
test_report.entry_date = pd.to_datetime(test_report.entry_date)
test_report['holding'] = test_report.exit_date-test_report.entry_date

In [211]:
test_report

stock_id entry_date  exit_date entry_sig_date exit_sig_date  position  \
0     3303 岱稜 2015-09-21 2015-09-30     2015-09-18    2015-09-25       0.1   
1     3303 岱稜 2015-09-30 2015-10-05     2015-09-25    2015-10-02       0.1   
2     3303 岱稜 2015-10-05 2015-10-12     2015-10-02    2015-10-08       0.1   
3     3303 岱稜 2015-10-12 2015-10-19     2015-10-08    2015-10-16       0.1   
4     3303 岱稜 2015-10-19 2015-10-26     2015-10-16    2015-10-23       0.1   
...       ...        ...        ...            ...           ...       ...   
3016  1569 濱川 2024-12-02        NaT     2024-11-29           NaT       0.1   
3017  3450 聯鈞 2024-12-02        NaT     2024-11-29           NaT       0.1   
3018  4956 光鋐 2024-12-02        NaT     2024-11-29           NaT       0.1   
3019  6214 精誠        NaT        NaT     2024-12-08           NaT       NaN   
3020  9938 百和        NaT        NaT     2024-12-08           NaT       NaN   

      period  entry_index  exit_index    return  ... turnover@exit_date  \
0        5.0       2091.0      2096.0  0.010631  ...       1.062880e+07   
1        3.0       2096.0      2099.0 -0.030220  ...       2.753418e+06   
2        4.0       2099.0      2103.0  0.050992  ...       2.052094e+07   
3        5.0       2103.0      2108.0 -0.018868  ...       2.530018e+06   
4        5.0       2108.0      2113.0  0.016484  ...       3.109776e+06   
...      ...          ...         ...       ...  ...                ...   
3016     5.0       4335.0        -1.0 -0.020062  ...       9.271438e+07   
3017     5.0       4335.0        -1.0  0.034560  ...       5.365832e+09   
3018     5.0       4335.0        -1.0  0.047753  ...       4.622545e+08   
3019     NaN          NaN         NaN       NaN  ...       2.164063e+09   
3020     NaN          NaN         NaN       NaN  ...       3.006653e+08   

      volume@entry_date  volume@exit_date  警示股@entry_date  處置股@entry_date  \
0              745250.0          584000.0           False           False   
1              584000.0          156001.0           False           False   
2              156001.0         1106250.0           False           False   
3             1106250.0          139012.0           False           False   
4              139012.0          168096.0           False           False   
...                 ...               ...             ...             ...   
3016          3144343.0         1460069.0           False            True   
3017         28602055.0        21377818.0           False           False   
3018          3341573.0        12392882.0           False           False   
3019         13783839.0        13783839.0           False           False   
3020          3666650.0         3666650.0           False           False   

      全額交割股@entry_date  警示股@exit_date  處置股@exit_date  全額交割股@exit_date  holding  
0                False          False          False            False   9 days  
1                False          False          False            False   5 days  
2                False          False          False            False   7 days  
3                False          False          False            False   7 days  
4                False          False          False            False   7 days  
...                ...            ...            ...              ...      ...  
3016             False          False           True            False      NaT  
3017             False          False          False            False      NaT  
3018             False          False          False            False      NaT  
3019             False          False          False            False      NaT  
3020             False          False          False            False      NaT  

[3021 rows x 26 columns]

In [221]:
close =close[close.index>='2014-01-01']
# 營收成長
c1 = (revenue.pct_change().average(6) > 0).index_str_to_date()
c2 = close.rolling(20).min() > close.rolling(20).max() * 0.7
# 成交量與價格收縮
volumereduce = volume.average(10) < (volume.average(60)*0.5)
pricecontract = close.rolling(10).std() < (close.rolling(60).std()*0.5)

# VCP = 價量收縮、創新高、有足夠成交量
vcp = (volumereduce & pricecontract).sustain(5, 1) & (close == close.rolling(100).max()) & (volume >= volume.rolling(20).mean()*0.8)

# 總體部位
# 進場：(c1, c2, vcp, 流動性足夠, 長期均向上)
# 出場：股價 < 季線
buy = (vcp & c1 & c2 & (volume*close > 2000000) & (close > close.average(250)))
sell = close < close.average(60)

p = buy.hold_until(sell, nstocks_limit=10, rank=(revenue / revenue.average(3)).replace([np.inf, -np.inf], np.nan).index_str_to_date())

# 回測
test_report, r = backtest.sim(p, fee_ratio=1.425/1000/3, position_limit=0.1, resample='W', stop_loss=0.1)
test_report.exit_date = pd.to_datetime(test_report.exit_date)
test_report.entry_date = pd.to_datetime(test_report.entry_date)
test_report['holding'] = test_report.exit_date-test_report.entry_date

Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip install finlab==None" to update the latest version.
Your version is 1.2.16, please install a newer version.
Use "pip

In [217]:
def trading_result(data_result):
    
    data_result.loc[:, '交易筆數'] = np.where(data_result['return'], 1, 0)
    data_result['持有天數']= data_result.holding.astype(int)
    data_result['勝率'] = np.where(data_result['return'] >= 0, 1, 0)
    data_result['勝報酬'] = data_result[data_result['return'] >= 0]['return']
    data_result['敗報酬'] = data_result[data_result['return'] < 0]['return']
    data_result['均筆報酬'] = data_result['return']


    # 計算整個數據集的交易結果
    overall_data_result = pd.DataFrame(data_result.agg({'交易筆數':'sum', '持有天數':'mean','勝率':'mean', 
                                                   '勝報酬':'mean', '敗報酬':'mean', 
                                                   '均筆報酬':'mean'}), columns=['Benchmark']).transpose()
    
    # 計算賺賠比和凱莉值
    overall_data_result['賺賠比'] = round(overall_data_result['勝報酬'].astype(float)/abs(overall_data_result['敗報酬'].astype(float)),2)
    overall_data_result['凱莉值'] = round((overall_data_result['勝率'] - ((1 - overall_data_result['勝率'])/overall_data_result['賺賠比'])),4)

    
    # round資料
    overall_data_result['持有天數']=round(overall_data_result['持有天數'],0)

    # 重排列順序
    overall_data_result = overall_data_result[['交易筆數','勝率', '勝報酬', '敗報酬', '均筆報酬','賺賠比', '凱莉值','持有天數']]

    return overall_data_result.transpose()

In [225]:
test_report['return'].mean()

0.006566577213197831

In [223]:
trading_result(test_report)

Benchmark
交易筆數  4.053000e+03
勝率    5.019503e-01
勝報酬   5.500340e-02
敗報酬  -4.239338e-02
均筆報酬  6.566577e-03
賺賠比   1.300000e+00
凱莉值   1.188000e-01
持有天數 -2.189006e+16

## Appemdix

## exmaple for rescaling

In [ ]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from datetime import timedelta

# Assuming normalize_window is a predefined function for normalizing the price window
def normalize_window(window):
    return (window - window.min()) / (window.max() - window.min())

# Assuming adj_close is your DataFrame containing the stock data
stock_data = adj_close[adj_close.code=='2330'].reset_index(drop=True)

# Ensure that stock_data has a DatetimeIndex
stock_data['date'] = pd.to_datetime(stock_data['date'])  # Convert to datetime if necessary
stock_data.set_index('date', inplace=True)  # Set the Date column as the index

# Ensure start_date and end_date are Timestamps
end_date = stock_data.index[-1]  # The last date in the stock data
start_date = end_date - timedelta(days=251)  # Define the window start

# Use .loc for slicing, and make sure the start and end dates are within the range of stock_data's index
window = stock_data.loc[start_date:end_date, 'adj_close']  # Extract 'adj_close' column over the time window

# Normalize the price window
normalized_prices = normalize_window(window)
normalized_time = np.linspace(0, 1, len(normalized_prices))  # Normalize time to the range [0, 1]

# Plot for Original Prices (P_T)
fig1 = go.Figure()

# Add original prices trace
fig1.add_trace(go.Scatter(
    x=window.index, y=window,
    mode='lines',
    name='Original Prices (P_T)',  # Label for original prices
    line=dict(color='gray')
))

fig1.update_layout(
    title=f'2330.TW Original Adjusted Stock Prices for {end_date.strftime("%Y-%m-%d")}',
    xaxis_title='Date',
    yaxis_title='Price',
    # template='plotly_white',
    hovermode='x unified'  # Show hover information for all traces at the same x-axis point
)

# Show the first figure (Original Prices)
fig1.show()

# Plot for Normalized Prices (\widetilde{P_T}) (Square plot)
fig2 = go.Figure()

# Add normalized prices trace
fig2.add_trace(go.Scatter(
    x=normalized_time, y=normalized_prices,
    mode='lines',
    name='Normalized Prices (\\widetilde{P_T})',  # Label for normalized prices
    line=dict(color='red', dash='dash')
))

fig2.update_layout(
    title=f'2330.TW Normalized Adjusted Stock Prices for {end_date.strftime("%Y-%m-%d")}',
    xaxis_title='Normalized Time (0-1)',
    yaxis_title='Normalized Price',
    # template='plotly_white', 
    hovermode='x unified',  # Show hover information for all traces at the same x-axis point
    xaxis=dict(range=[0, 1]),  # Ensure x-axis is between 0 and 1
    yaxis=dict(range=[0, 1]),  # Ensure y-axis is between 0 and 1
    width=600,  # Set the width to make the plot square
    height=600  # Set the height to make the plot square
)


# Show the second figure (Normalized Prices)
fig2.show()
